In [0]:
%sql

use workspace.reddit;
SHOW VOLUMES;

database volume_name reddit all_data_bronze

In [0]:
from pyspark.sql import SparkSession


spark = SparkSession.builder.getOrCreate()

df_posts_bronze = spark.read.parquet("/Volumes/workspace/reddit/all_data_bronze/all_cleaned_posts.parquet")
df_comments_bronze = spark.read.parquet("/Volumes/workspace/reddit/all_data_bronze/all_cleaned_comments.parquet")

df_posts_bronze.printSchema()


root
 |-- post_id: string (nullable = true)
 |-- title: string (nullable = true)
 |-- author: string (nullable = true)
 |-- score: long (nullable = true)
 |-- num_comments: long (nullable = true)
 |-- created_at: date (nullable = true)
 |-- post_content: string (nullable = true)
 |-- subreddit: string (nullable = true)
 |-- source: string (nullable = true)



In [0]:
%sql
drop table if exists reddit.posts_bronze ;
drop table if exists reddit.comments_bronze;

CREATE TABLE reddit.posts_bronze
SELECT * FROM read_files(
  '/Volumes/workspace/reddit/all_data_bronze/all_cleaned_posts.parquet',
  format=>'parquet'
) ;


CREATE TABLE reddit.comments_bronze
SELECT * FROM read_files(
  '/Volumes/workspace/reddit/all_data_bronze/all_cleaned_comments.parquet',
  format=>'parquet'
) ;




num_affected_rows num_inserted_rows

In [0]:
%sql
select * from posts_bronze limit 10;

post_id title author score num_comments created_at post_content subreddit source _rescued_data 1fywi9h 2024 Nobel Prize for Physics goes to ML and DNN researchers J. Hopfield and G. Hinton PrittEnergizer 1161 306 2024-10-08 Announcement: https://x.com/NobelPrize/status/1843589140455272810

Our boys John Hopfield and Geoffrey Hinton were rewarded for their foundational contributions to machine learning and deep learning with the Nobel prize for physics 2024!

I hear furious Schmidhuber noises in the distance!

On a more serious note, despite the very surprising choice, I am generally happy - as a physicist myself with strong interest in ML, I love this physics-ML cinematic universe crossover.

The restriction to Hopfield and Hinton will probably spark discussions about the relative importance of {Hopfield, Hinton, LeCun, Schmidhuber, Bengio, Linnainmaa, ...} for the success of modern ML/DL/AI.
A discussion especially Schmidhuber very actively engages in.

The response from the core physics community however is rather mixed, as shown in the [/r/physics thread](https://www.reddit.com/r/Physics/comments/1fyw12p/the_2024_nobel_prize_in_physics_is_awarded_to/). There, the missing link/connection to physics research is noted and the concurrent "loss" of the '24 prize for physics researchers. MachineLearning t null 1g7dzkp Why do PhD Students in the US seem like overpowered final bosses Unknown 1119 271 2024-10-19 Hello,

I'm a PhD student in a European university, working on AI/ML/CV ..etc. my PhD is 4 years. The first year I literally just spent learning how to actually do research, teaching one course to learn how things work...etc. Second year, I published my first publication as a co-author in CVPR. By third year, I can manage research projects, I understand how to do grants applications, how funding works, the politics of it all ...etc. I added to my CV, 2 publications, one journal and another conference as first author. I'm very involved in industry and I also write a lot of production grade code in regard to AI, systems architecture, backend, cloud, deployment, etc for companies that have contracts with my lab.

The issue is when I see PhD students similar to me in the US, they be having 10 publications, 5 of them 1st author, all of them are either CVPR, ICML, ICLR, NeurIPS ...etc. I don't understand, do these people not sleep ? How are they able to achieve this crazy amount of work and still have 3 publications every year in A\* journals ?

I don't think these people are smarter than I, usually I get ideas and I look up if something exists, and I can see that something was just published by some PhD student in Stanford or DeepMind ..etc like 1 month ago, So I can see that my reasoning isn't late in regard to SOTA. but the concepts that you would need to grasp to just have one of those publications + the effort and the time you need to invest and the resources to get everything done, wouldn't be possible for 2\~3 months project. How is it possible for these people to do this ?

Thank you ! MachineLearning t null 1h7jg87 Stuck in AI Hell: What to do in post LLM world Educational_News_371 845 220 2024-12-05 
Hey Reddit,

I’ve been in an AI/ML role for a few years now, and I’m starting to feel disconnected from the work. When I started, deep learning models were getting good, and I quickly fell in love with designing architectures, training models, and fine-tuning them for specific use cases. Seeing a loss curve finally converge, experimenting with layers, and debugging training runs—it all felt like a craft, a blend of science and creativity. I enjoyed implementing research papers to see how things worked under the hood. Backprop, gradients, optimization—it was a mental workout I loved.

But these days, it feels like everything has shifted. LLMs dominate the scene, and instead of building and training models, the focus is on using pre-trained APIs, crafting prompt chains, and setting up integrations. Sure, there’s engineering in

In [0]:
%sql
select * from comments_bronze  
where author =='None' and comment_content=='[deleted]'
limit 10;

comment_id author comment_content score created_at post_id source _rescued_data lqxzt86 None [deleted] 276 2024-10-08 t3_1fywi9h t null m0ls3xs None [deleted] 49 2024-12-05 t3_1h7jg87 t null lrsmhnt None [deleted] 35 2024-10-13 t3_1g31hfd t null m0vvl26 None [deleted] 94 2024-12-07 t3_1h8nhbh t null lq27dl6 None [deleted] 16 2024-10-03 t3_1fujbuz t null lealmz2 None [deleted] 32 2024-07-21 t3_1e8v2za t null lr3kprl None [deleted] 147 2024-10-09 t3_1fznaa9 t null lg6loli None [deleted] 40 2024-08-02 t3_1eifnvj t null l35znn1 None [deleted] 16 2024-05-08 t3_1cmwljs t null l33vzgb None [deleted] 12 2024-05-08 t3_1cmwljs t null

In [0]:
from pyspark.sql.functions import col, lower, length, when
#removing comments with no author and no content

df_comments_silver = df_comments_bronze.filter((col('author') != 'None') & (col('comment_content') != '[deleted]'))

In [0]:
%sql
select comment_id, comment_content from comments_bronze 

comment_id comment_content l2j2en6 Yes, they train the models to approximate the distribution of the training set. Once models are big enough, given the same dataset they should all converge to roughly the same thing. As I understand it, the main advantage of architectures like transformers is that they can learn the distribution with fewer layers and weights, and converge faster, than simpler architectures. l2ja8g9 “With enough weights” is doing a lot of heavy lifting here. l2j0k7e I'm genuinely surprised this person got a job at OpenAI if they didn't know that datasets and compute are pretty much the only thing that matters in ML/AI. Sutton's Bitter Lesson came out like over 10 years ago. Tweaks in hyperparams and architecture can squeeze you out a SOTA performance by some tiny margin, but it's all about the quality of the data. l2j3w87 Architectures and optimizers have a role to an extent. As I said before in theory a CNN and a Dense Layer only network can get the job done about the same. However, we prefer CNNs in images. Because they are more efficient.

Using RMSProp vs SGD has an impact on efficiency.

There is the dataset and then there is the performance per parameter, efficiency of training, memory requirements and so on. 

There are multiple approaches for solving the same problem. This is true for all statistics, data science and programming since their very existence.

Some architectures are lighter, some are good with bigger data, some activation functions are converging better than others. 

Even the loss function matters. In fact imo, it is the second most important thing, with the dataset being the first.

Even how you'll represent the data in your model matters. This also something often overlooked by beginners. l2j1t9q Ring of truth but I think it's risky to "over-index". The architecture of the fully connected layers doesn't matter much but transformers, convnets, etc have very different characteristics in terms of how training and inference can be structured. Heck, just making the operation more understandable to humans is important and architecture can help there. 

This reads to me like a lighthouse keeper who stared at the light too long. It's not "untrue" but it's less profound than it sounds and has limits. l2j3go4 Isn't this obvious? Neural nets are function approximators, and the functions they approximate are defined by the dataset. Any sufficiently large model will just interpolate/extrapolate the dataset in pretty much the same way. Things are more interesting with smaller models, because they can compete to have better/closer approximations. l2j3x6k Run a logistic regression on large dataset and get back to me. lqxfb1o Respectable Physicists aren't going to be pleased. Brings to mind the Hitchhikers Guide quote... :-p

>*Many respectable physicists said that they weren't going to stand for this − partly because it was a debasement of science, but mostly because they didn't get invited to those sort of parties.*

>*Another thing they couldn't stand was the perpetual failure they encountered in trying to construct a machine which could generate the infinite improbability field needed to flip a spaceship across the mind-­‐paralyzing distances between the furthest stars, and in the end they grumpily announced that such a machine was virtually impossible.*

>*Then, one day, a student who had been left to sweep up the lab after a particularly unsuccessful party found himself reasoning this way:*

>*If, he thought to himself, such a machine is a virtual impossibility, then it must logically be a finite improbability. So all I have to do in order to make one is to work out exactly how improbable it is, feed that figure into the finite improbability generator, give it a fresh cup of really hot tea... and turn it on!*

>*He did this, and was rather startled to discover that he had managed to create the long sought after golden Infinite Improbability generator out of thin air.*

>*It startled him even more

In [0]:
# to delete emojiesss 
from pyspark.sql.functions import regexp_replace, col

emoji_pattern = r"[\U0001F600-\U0001F64F" \
                r"\U0001F650-\U0001F67F" \
                r"\U0001F680-\U0001F6FF" \
                r"\U0001F300-\U0001F5FF" \
                r"\U0001F1E0-\U0001F1FF" \
                r"\u2600-\u26FF\u2700-\u27BF]"

df_posts_silver = df_posts_bronze.withColumn(
    "post_content",
    regexp_replace(col("post_content"), "[^\\x00-\\x7F]", "")
)

df_comments_silver = df_comments_silver.withColumn(
    "comment_content",
    regexp_replace(col("comment_content"), "[^\\x00-\\x7F]", "")
)

df_comments_silver.filter(col('comment_id')=='m1qw6cw').collect() #an example after removing emojies


[Row(comment_id='m1qw6cw', author='Briskfall', comment_content="*grabs popcorn* \n\nOh, that guy? When I first heard of him never knew that it was for a personal project ohhh people speculated that it was for his role at his job. If so then yikes... It's like all the cryptobros diverting compute to mine coins... No way he's getting away with it. You don't set a precedence, then it'll be a floodgate of copycats...", score=68, created_at=datetime.date(2024, 12, 12), post_id='t3_1hctf36', source='t')]

In [0]:
import pyspark.sql.functions as F
from pyspark.sql.types import StringType
import re

def clean_text(text):
    if text is None:
        return None
    text = re.sub(r'<[^>]+>', ' ', text)  # removing HTML tags
    text = re.sub(r'http\S+|www\.\S+', ' ', text)  #removing URLs
    text = re.sub(r'[@#]\w+', ' ', text)  #removing mentions & hashtags
    text = re.sub(r'[^\w\s]', ' ', text)  # removing other punctuations
    text = text.lower()  # lowercase
    text = re.sub(r'\s+', ' ', text).strip()  #removing extra spaces
    return text

clean_text_udf = F.udf(clean_text, StringType())

df_posts_silver = df_posts_silver.withColumn(
    "post_content_clean", clean_text_udf(F.col("post_content"))
)

df_comments_silver = df_comments_silver.withColumn(
    "comment_content_clean", clean_text_udf(F.col("comment_content"))
)
#lwd3joi 
df_comments_silver.filter(col('comment_id')=='lm544z7').collect()

[Row(comment_id='lm544z7', author='DarthLoki79', comment_content="[https://github.com/xwying/torchshow](https://github.com/xwying/torchshow)\n\nPlease don't touch PyTorch types haha - otherwise looks really neat.", score=13, created_at=datetime.date(2024, 9, 8), post_id='t3_1fbz318', source='t', comment_content_clean='please don t touch pytorch types haha otherwise looks really neat')]

In [0]:
df_posts_silver.createOrReplaceTempView("posts_silver")
df_comments_silver.createOrReplaceTempView("comments_silver")

In [0]:
df_comments_silver.printSchema()
df_posts_silver.printSchema()


root
 |-- comment_id: string (nullable = true)
 |-- author: string (nullable = true)
 |-- comment_content: string (nullable = true)
 |-- score: long (nullable = true)
 |-- created_at: date (nullable = true)
 |-- post_id: string (nullable = true)
 |-- source: string (nullable = true)
 |-- comment_content_clean: string (nullable = true)

root
 |-- post_id: string (nullable = true)
 |-- title: string (nullable = true)
 |-- author: string (nullable = true)
 |-- score: long (nullable = true)
 |-- num_comments: long (nullable = true)
 |-- created_at: date (nullable = true)
 |-- post_content: string (nullable = true)
 |-- subreddit: string (nullable = true)
 |-- source: string (nullable = true)
 |-- post_content_clean: string (nullable = true)



In [0]:
df = spark.sql(
"""
SELECT comment_id,comment_content_clean
FROM comments_silver
limit 30
""")

display(df)


comment_id comment_content_clean l2j2en6 yes they train the models to approximate the distribution of the training set once models are big enough given the same dataset they should all converge to roughly the same thing as i understand it the main advantage of architectures like transformers is that they can learn the distribution with fewer layers and weights and converge faster than simpler architectures l2ja8g9 with enough weights is doing a lot of heavy lifting here l2j0k7e i m genuinely surprised this person got a job at openai if they didn t know that datasets and compute are pretty much the only thing that matters in ml ai sutton s bitter lesson came out like over 10 years ago tweaks in hyperparams and architecture can squeeze you out a sota performance by some tiny margin but it s all about the quality of the data l2j3w87 architectures and optimizers have a role to an extent as i said before in theory a cnn and a dense layer only network can get the job done about the same however we prefer cnns in images because they are more efficient using rmsprop vs sgd has an impact on efficiency there is the dataset and then there is the performance per parameter efficiency of training memory requirements and so on there are multiple approaches for solving the same problem this is true for all statistics data science and programming since their very existence some architectures are lighter some are good with bigger data some activation functions are converging better than others even the loss function matters in fact imo it is the second most important thing with the dataset being the first even how you ll represent the data in your model matters this also something often overlooked by beginners l2j1t9q ring of truth but i think it s risky to over index the architecture of the fully connected layers doesn t matter much but transformers convnets etc have very different characteristics in terms of how training and inference can be structured heck just making the operation more understandable to humans is important and architecture can help there this reads to me like a lighthouse keeper who stared at the light too long it s not untrue but it s less profound than it sounds and has limits l2j3go4 isn t this obvious neural nets are function approximators and the functions they approximate are defined by the dataset any sufficiently large model will just interpolate extrapolate the dataset in pretty much the same way things are more interesting with smaller models because they can compete to have better closer approximations l2j3x6k run a logistic regression on large dataset and get back to me lqxfb1o respectable physicists aren t going to be pleased brings to mind the hitchhikers guide quote p many respectable physicists said that they weren t going to stand for this partly because it was a debasement of science but mostly because they didn t get invited to those sort of parties another thing they couldn t stand was the perpetual failure they encountered in trying to construct a machine which could generate the infinite improbability field needed to flip a spaceship across the mind paralyzing distances between the furthest stars and in the end they grumpily announced that such a machine was virtually impossible then one day a student who had been left to sweep up the lab after a particularly unsuccessful party found himself reasoning this way if he thought to himself such a machine is a virtual impossibility then it must logically be a finite improbability so all i have to do in order to make one is to work out exactly how improbable it is feed that figure into the finite improbability generator give it a fresh cup of really hot tea and turn it on he did this and was rather startled to discover that he had managed to create the long sought after golden infinite improbability generator out of thin air it startled him even more when just after he was awarded the galactic institute s prize for extreme cleverness he got lynched by a rampa

In [0]:

df_comments_silver.write.mode("overwrite").saveAsTable("comments_silver")

df_posts_silver.write.mode("overwrite").saveAsTable("posts_silver")


#Silver Layer done 

In [0]:
df_posts_gold = df_posts_silver
df_comments_gold = df_comments_silver

In [0]:
'''from pyspark.ml.feature import StopWordsRemover

remover = StopWordsRemover().setInputCol("post_content_clean").setOutputCol("post_content_no_stopwords")

df_posts_gold_words_count = remover.transform(df_posts_gold_words_count)

remover_comments = StopWordsRemover().setInputCol("comment_content_clean").setOutputCol("comment_content_no_stopwords")

df_comments_gold_words_count = remover_comments.transform(df_comments_gold_words_count)'''

'from pyspark.ml.feature import StopWordsRemover\n\nremover = StopWordsRemover().setInputCol("post_content_clean").setOutputCol("post_content_no_stopwords")\n\ndf_posts_gold_words_count = remover.transform(df_posts_gold_words_count)\n\nremover_comments = StopWordsRemover().setInputCol("comment_content_clean").setOutputCol("comment_content_no_stopwords")\n\ndf_comments_gold_words_count = remover_comments.transform(df_comments_gold_words_count)'

Top 10 Most Contributing Authors both posts and comments

In [0]:
df_most_contributing_authors_combined = spark.sql("""
SELECT author, 
       SUM(num_posts) AS total_posts, 
       SUM(num_comments) AS total_comments,
       (SUM(num_posts) + SUM(num_comments)) AS total_activity
FROM (
    SELECT author, COUNT(*) AS num_posts, 0 AS num_comments
    FROM posts_silver
    WHERE author != 'Unknown'
    GROUP BY author

    UNION ALL

    SELECT author, 0 AS num_posts, COUNT(*) AS num_comments
    FROM comments_silver
    WHERE author != 'Unknown'
    GROUP BY author
) combined
GROUP BY author
ORDER BY total_activity DESC
LIMIT 10
""")

display(df_most_contributing_authors_combined)


author total_posts total_comments total_activity DigThatData 0 61 61 currentscurrents 2 59 61 Seankala 8 47 55 marr75 0 46 46 qalis 1 39 40 bregav 2 34 36 alexmlamb 2 28 30 bgighjigftuik 2 26 28 slashdave 0 28 28 Sad-Razzmatazz-5188 2 24 26

In [0]:
# Save the DataFrame as a managed table in your catalog
df_most_contributing_authors_combined.write.format("delta").mode("overwrite").saveAsTable("most_contributors_gold")


2- most trending topics (ML ,DL ,LLM)

In [0]:
"""
an idea

import pyspark.sql.functions as F


keywords = [
    "ml", "machine learning", 
    "deep learning", "dl",
    "llms","llm", "gpt","gpts","genai", "generative ai"
]


keywords = [k.lower() for k in keywords]


def keyword_counts(df, col_name):
    results = []
    for kw in keywords:
        count = df.filter(F.lower(F.col(col_name)).contains(kw)).count()
        results.append((kw, count))
    return results


post_counts = keyword_counts(df_posts_gold_words_count, "post_content_clean")


comment_counts = keyword_counts(df_comments_gold_words_count, "comment_content_clean")


print("=== Posts Keyword Counts ===")
for kw, cnt in post_counts:
    print(f"{kw}: {cnt}")

print("\n=== Comments Keyword Counts ===")
for kw, cnt in comment_counts:
    print(f"{kw}: {cnt}")
"""

=== Posts Keyword Counts ===
ml: 404
machine learning: 198
deep learning: 114
dl: 216
datascience: 4
data science: 29
transformers: 90
llms: 207
gpt: 168
genai: 5
generative ai: 4

=== Comments Keyword Counts ===
ml: 875
machine learning: 268
deep learning: 201
dl: 385
datascience: 11
data science: 51
transformers: 157
llms: 302
gpt: 252
genai: 7
generative ai: 11


In [0]:
from pyspark.sql.functions import col, lower, lit, when, sum as spark_sum, date_format

df_posts_gold_words_count = df_posts_silver.select("created_at", "post_content_clean")
df_comments_gold_words_count = df_comments_silver.select("created_at", "comment_content_clean")

# 1- Define category mapping
keyword_mapping = {
    "ml": "ML",
    "machine learning": "ML",
     "machinelearning": "ML",
    "deep learning": "DL",
    "deeplearning": "DL",
    "dl": "DL",
    "llms": "GenAI",
    "llm": "GenAI",
    "gpt": "GenAI",
    "gpts": "GenAI",
    "genai": "GenAI",
    "generative ai": "GenAI"
}

# 2- Function to detect category
def get_category_expr(text_col):
    expr = None
    for kw, cat in keyword_mapping.items():
        condition = lower(text_col).like(f"%{kw}%")
        if expr is None:
            expr = when(condition, lit(cat))
        else:
            expr = expr.when(condition, lit(cat))
    return expr

# 3- Apply for posts
df_posts_trend = df_posts_gold_words_count.withColumn(
    "category", get_category_expr(col("post_content_clean"))
).withColumn("month", date_format(col("created_at"), "yyyy-MM"))

# 4- Apply for comments
df_comments_trend = df_comments_gold_words_count.withColumn(
    "category", get_category_expr(col("comment_content_clean"))
).withColumn("month", date_format(col("created_at"), "yyyy-MM"))

# 5- Union and aggregate
df_trend_all = df_posts_trend.select("month", "category") \
    .union(df_comments_trend.select("month", "category")) \
    .filter(col("category").isNotNull()) \
    .groupBy("month", "category") \
    .agg(spark_sum(lit(1)).alias("mentions")) \
    .orderBy("month", "mentions", ascending=[True, False])

df_trend_all.show(50, truncate=False)


+-------+--------+--------+
|month  |category|mentions|
+-------+--------+--------+
|2011-11|ML      |6       |
|2012-06|ML      |1       |
|2013-06|ML      |2       |
|2013-07|DL      |1       |
|2013-07|ML      |1       |
|2013-11|ML      |3       |
|2014-01|ML      |1       |
|2014-04|ML      |2       |
|2014-05|ML      |1       |
|2014-12|ML      |2       |
|2015-02|ML      |3       |
|2015-03|ML      |1       |
|2015-04|ML      |1       |
|2015-05|ML      |2       |
|2015-05|DL      |1       |
|2015-06|DL      |3       |
|2015-06|ML      |2       |
|2015-07|DL      |6       |
|2015-07|ML      |6       |
|2015-08|ML      |3       |
|2015-09|ML      |1       |
|2015-10|ML      |12      |
|2015-10|DL      |4       |
|2015-11|DL      |3       |
|2015-12|ML      |4       |
|2015-12|DL      |1       |
|2016-01|ML      |4       |
|2016-01|DL      |3       |
|2016-02|ML      |6       |
|2016-02|DL      |1       |
|2016-03|ML      |14      |
|2016-03|DL      |9       |
|2016-04|ML      |6 

In [0]:
# Save the DataFrame as a managed table in your catalog
df_trend_all.write.format("delta").mode("overwrite").saveAsTable("most_trending_topics_gold")


3_most trending GPT (chat or gemini)?

In [0]:
from pyspark.sql.functions import col, lower, lit, when, sum as spark_sum, date_format

# Subkeywords for GenAI
genai_keywords = {
    "chatgpt": "ChatGPT",
    "chat-gpt": "ChatGPT",
    "gemini": "Gemini",
    "grok": "Grok"
}

def get_genai_expr(text_col):
    expr = None
    for kw, name in genai_keywords.items():
        condition = lower(text_col).like(f"%{kw}%")
        if expr is None:
            expr = when(condition, lit(name))
        else:
            expr = expr.when(condition, lit(name))
    return expr


# Apply same genai_sub extraction for posts
df_posts_genai_total = df_posts_gold_words_count.withColumn(
    "genai_sub", get_genai_expr(col("post_content_clean"))
).filter(col("genai_sub").isNotNull())

# Apply for comments
df_comments_genai_total = df_comments_gold_words_count.withColumn(
    "genai_sub", get_genai_expr(col("comment_content_clean"))
).filter(col("genai_sub").isNotNull())

# Union posts and comments
df_genai_total = df_posts_genai_total.select("genai_sub") \
    .union(df_comments_genai_total.select("genai_sub")) \
    .groupBy("genai_sub") \
    .agg(spark_sum(lit(1)).alias("total_mentions")) \
    .orderBy(col("total_mentions").desc())

df_genai_total.show(truncate=False)

+---------+--------------+
|genai_sub|total_mentions|
+---------+--------------+
|ChatGPT  |123           |
|Gemini   |44            |
|Grok     |15            |
+---------+--------------+



In [0]:
df_genai_total.write.format("delta").mode("overwrite").saveAsTable("most_trending_GPT_gold")
